In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
#Topic URLs from which Articles URLs to be scrapped

InitURLs = {
         'معیشت':'c95y3y8vrqqt', 'پاکستان':'cjgn7n9zzq7t', 'آس پاس':'cl8l9mveql2t',
        'ورلڈ':'cw57v2pmll9t', 'کھیل':'c340q0p2585t', 'فن فنکار':'ckdxnx900n5t',
        'کورونا وائرس':'cezpppg7l0pt', 'فیشن':'c95y3y8yxk7t', 'سیاست':'ckdxnx9z2j6t',
        'پاکستان تحریکِ انصاف':'cg72628zvzkt', 'عمران خان':'cwr9j9x31nkt', 'پاکستان مسلم لیگ':'c95y3y8r1gzt',
        'پاکستان پیپلز پارٹی':'c2dwqwz087zt', 'طب':'c1gdqdprqggt', 'سائنس':'c40379e2ymxt',
        'سفر':'cdr5653vdndt', 'صحت':'cwr9j9x3kkqt', 'سوشل میڈیا':'cdr565397xpt',
        'ٹوئٹر':'c5qvpv32zr5t', 'خواتین': 'cg72628d5vzt', 'جرم':'cnq686jyxnvt',
        'بھارت':'c1gdqdpv558t','پولیس':'cvjp2pxdw97t', 'لاہور':'c6vzyzw02znt',
        'پنجاب':'c5qvpv35597t', 'تاریخ':'c1gdqdpypg4t' , 'فلسطین' : 'cjgn7n9zxzvt' , 'اسرائیل': 'cr50y0pdp35t',
        'سندھ': 'cnq686jpd74t', 'تشدد': 'c6vzyz2wqgpt' , 'انٹرنیٹ':'c06gqgvd3w1t', 'ملازمتیں': 'c5qvpvn3q0jt',
         'نوجوان': 'c7zp5p44qwrt', 'ٹیکنالوجی': 'c8y94952w2zt' , 'پاکستان کا پارلیمان': 'c404v4gygvrt'
       }

In [ ]:
import requests
import json
import pandas as pd
import time
from bs4 import BeautifulSoup as bs
import re
import json
import click
import time
import random
import os

In [ ]:
drivePath = '/content/drive/MyDrive/Urdu/BBC New/'

In [ ]:
# Func for URL Retrieval
def make_soup(url):
    doc = requests.get(url)
    if str(doc) == "<Response [200]>":
        # create a soup object that contains the navigable html presentation of the page
        soup = bs(doc.content, 'html.parser')
        print(f"Retrieved url: {url}")
        return soup
    else:
        print(f"{url} cannot be reached.")

# Func for URL Const from Topic
def topic_URLConst(topic):
    base_url = 'https://www.bbc.com/urdu/topics/'
    return base_url+topic+'?page='

# Func for reading jsonl i.e. Topics and Summaries
def read_jsonl(file_name):
  json_data = []
  #Opening JSON file for finding links for retrieval
  with open(file_name, 'r', encoding='utf-8') as f:
    for line in f:
      json_data.append(json.loads(line))
  return json_data

# Func for saving Summaries to JSONL file
def save_summaries(page_objs):
    #Writing JSONL file of Scrapped Summaries in UTF-8 to get correct display of Urdu Chars
    name = 'Summaries.jsonl'

    existing_summaries = []
    if os.path.exists(drivePath+name):
      existing_summaries = read_jsonl(drivePath+name)

    for obj in page_objs:
      existing_summaries.append(obj)
    with open(drivePath+name, 'w', encoding='utf-8') as f:
      for s in existing_summaries:
        json.dump(s, f, ensure_ascii=False)
        f.write("\n")
    print(name,' file appended..with ', len(page_objs), ' records!')

def duplicate_initTopic(t_url):
  for topic in InitURLs:
    if InitURLs[topic] in t_url:
      return True
  return False


def save_log(count):
  name = 'log.txt'
  with open(drivePath+name, 'w') as f:
    f.write(str(count))
    f.write('\n')
    f.write('Scrapping through Summaries for Topics & Subsequent Summaries Scrapping!')


def main_topic(topic):
  main_topics = ['cjgn7n9zzq7t', 'cynd7qxprq0t', 'cl8l9mveql2t', 'cw57v2pmll9t', 'c340q0p2585t', 'ckdxnx900n5t', 'c40379e2ymxt' , 'c1gdqdpv558t', 'cdr565397xpt', 'cjgn7n9zxzvt', 'cr50y0pdp35t', 'cnq686jpd74t', 'c6vzyz2wqgpt']
  #print (topic['href'])
  for mt in main_topics:
    #print(mt)
    if mt in topic:
      return True
  return False


def save_topics(topics):
    name = 'Topics.jsonl'

    existing_topics = []
    if os.path.exists(drivePath+name):
      existing_topics = read_jsonl(drivePath+name)

    for t in topics:
      existing_topics.append(t)
    with open(drivePath+name, 'w', encoding='utf-8') as f:
      for t in existing_topics:
        json.dump(t, f, ensure_ascii=False)
        f.write("\n")
    print(name,' file appended..with ', len(topics), ' records!')


def find_taggedTopics(a_url):
  name = 'Topics.jsonl'
  check_duplicate = False
  if os.path.exists(drivePath+name):
    existing_topics = read_jsonl(drivePath+name)
    check_duplicate = True

  scrp_topics = []
  base_url = 'https://www.bbc.com'
  soup = make_soup(a_url)

  topics = soup.find_all("a", href=re.compile("/urdu/topics/"))
  #print(topics)
  for t in topics:
    tmp = {}
    if main_topic(t['href']):
      continue
    if duplicate_initTopic(t['href']):
      continue
    if check_duplicate:
      for et in existing_topics:
        if et['t_url'] in t['href']:
          continue

    tmp['t_url'] = t['href'].replace('/urdu/topics/', '')
    tmp['t_name'] = t.get_text()

    scrp_topics.append(tmp)
  save_topics(scrp_topics)
  return scrp_topics

In [ ]:
# Func for extracting Summaries by iterating through pages of URL const from Topic
def extract_summaries(topic_url, category):
    #Get Existing Summaries for duplicate check
    duplicate = False
    name = 'Summaries.jsonl'
    check_duplicate = False
    if os.path.exists(drivePath+name):
      existing_summaries = read_jsonl(drivePath+name)
      check_duplicate = True

    #Loop through 40 x Pages (max on BBCUrdu Website) of Topic
    page_objs = []
    no_summaries = 0 #for counting empty pages without summaries
    for idx in range(40):
        if no_summaries == 5: #Three consecutive pages without summaries
          break
        #Adding Page Number at end of URL
        url = topic_url+str(idx+1)
        #Retrieval and Parsing through func make_soup
        if make_soup(url) is not None:
          soup = make_soup(url)
        else:
          continue #if can't find soup skip to next
        #Finding required Script through Regex in which Urdu article summaries are present
        #print(soup)
        pattern = re.compile('\"summaries\":\[(.*?)\}\]', re.MULTILINE | re.DOTALL)
        script = soup.find("script", text=pattern)
        #print(script.text)
        if(script == None):
          print('No Summaries Found at Page No : ', idx+1)
          no_summaries += 1
          continue #if can't find summaries URLs skip to next
        result = pattern.search(script.text).group(1)
        #adding braces to make it a valid json as present in weblink
        result = '[' + result + '}]'
        #Converting result to JSON
        try:
          result_json = json.loads(result)
        except:
          continue

        #Writing into Dict
        for i in result_json:
          temp_dict = {}
          if('type' in i):
            if i['type'] == 'article':
              if('link' in i):
                temp_dict['url'] = i['link']
              else:
                continue

              if('description' in i):
                temp_dict['summary'] = i['description']
              else:
                continue
              if('title' in i):
                temp_dict['title'] = i['title']
              if('firstPublished' in i):
                temp_dict['firstPublished'] = i['firstPublished']
              if('id' in i):
                temp_dict['id'] = i['id']
              if('category' in i):
                temp_dict['category'] = i['category']

          if 'url' not in temp_dict or 'summary' not in temp_dict:
            continue

          if len(page_objs) > 0:
            for obj in page_objs:
              if obj['url'] == temp_dict['url']:
                duplicate = True
                break

          if check_duplicate:
            for s in existing_summaries:
              if s['url'] == temp_dict['url']:
                duplicate = True
                break

          if duplicate == False:
            page_objs.append(temp_dict)
        #if click.confirm('Do you want to continue & save file?', default=True):
        #Adding random delay to avoid getting blocked by Websites; too many requests in same pattern
        #time.sleep(random.randint(5, 15))
    return page_objs

In [ ]:
for topic, address in InitURLs.items():
    topic_url = topic_URLConst(address)
    summaries = extract_summaries(topic_url, topic)
    save_summaries(summaries)


Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=1
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=1


<ipython-input-6-ed7295a2539c>:27: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  script = soup.find("script", text=pattern)


Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=2
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=2
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=3
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=3
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=4
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=4
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=5
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=5
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=6
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=6
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=7
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=7
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=8
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?page=8
Retrieved url: https://www.bbc.com/urdu/topics/c95y3y8vrqqt?pa

In [ ]:
name = 'Summaries.jsonl'
sum = read_jsonl(drivePath+name)
print(len(sum))
tmp = []
count = 0
for s in sum:
  duplicate = False
  if len(tmp)>0:
    for t in tmp:
      if t['url'] == s['url']:
        duplicate = True
        break
  if duplicate == False:
    tmp.append(s)

print(len(tmp))
for i in range(0,5):
  print(random.choice(tmp))

1856
1856
{'url': 'https://www.bbc.com/urdu/articles/cz48z7d17j7o', 'summary': 'سنہ 1766 کا ایک تھیٹر ٹوکن جو اس کے مالک کو لامحدود شوز تک رسائی دیتا ہے نیلام ہونے جا رہا ہے اور دلچسپ بات یہ ہے کہ جس کے پاس بھی یہ ٹوکن جائے گا وہ شخص آج بھی اس تھیٹر میں جا کر مفت کے شوز دیکھ سکتا ہے۔\n', 'title': '250 سال پرانا تھیٹر ٹوکن جسے آج بھی مفت شوز دیکھنے کے لیے استعمال کیا جا سکتا ہے', 'firstPublished': '2023-10-29T08:14:21.859Z', 'id': 'cz48z7d17j7o'}
{'url': 'https://www.bbc.com/urdu/articles/cq5py5ny5g8o', 'summary': 'نپولیئن کون تھا اور اس کی شخصیت اتنی متنازع کیوں ہے؟', 'title': 'جابر آمر یا اصلاح پسند بادشاہ: یورپ پر راج کرنے والے نپولین کا ہٹلر سے موازنہ کرنے پر فرانسیسی سیخ پا کیوں ہوئے؟', 'firstPublished': '2023-11-20T12:08:43.550Z', 'id': 'cq5py5ny5g8o'}
{'url': 'https://www.bbc.com/urdu/articles/c4nykd8w0ego', 'summary': 'انڈین ریاست چھتیس گڑھ کی ایک عدالت نے اپنی بیوی کے ساتھ غیر فطری انداز میں سیکس کرنے کا جرم ثابت ہونے پر شوہر کو 9 سال قید بامشقت اور 10 ہزار روپے جرمانے کی سزا س

In [ ]:
# It iterates through same articles most of the times..
name = 'Summaries.jsonl'
if os.path.exists(drivePath+name):
  existing_summaries = read_jsonl(drivePath+name)
count = 0
existing_summaries = random.choices(existing_summaries, k=100)
print(len(existing_summaries), ' x Total Articles to be Iterated Through')
if os.path.exists(drivePath+'log.txt'):
  with open(drivePath+'log.txt', 'r', encoding='utf-8') as f:
    for line in f:
      count = int(line)
      break
print('Starting from Article No ', count)
#existing_summaries = existing_summaries[32:]
for s in existing_summaries[count:]:
  count+=1
  print('Interating through Summary No ', count)
  tagged_topics = find_taggedTopics(s['url'])

  for topic in tagged_topics:
    topic_url = topic_URLConst(topic['t_url'])
    summaries = extract_summaries(topic_url, topic['t_name'])
    save_summaries(summaries)
  save_log(count)

100  x Total Articles to be Iterated Through
Starting from Article No  100


In [ ]:
# Func for extracting Summaries by iterating through pages of URL const from Topic
def extract_article(summary):
  #Constructing URL by adding url saved in summaries.json at end of base url
  url = make_URL(s['url'])
  soup = make_soup(s['url'])
  paras = []
  #Finding all <p> paragraphs in retrieved url
  for data in soup.find_all("p"):
    copy_flag = True
    #Finding urls in <p> paragraphs
    link = data.find('a')
    text = data.get_text()
    #Removing extras, pics text, urls, additional text (ads)
    if ('تصویر کا ذریعہ' in text):
      copy_flag = False
    elif ('بی بی سی بیرونی ویب سائٹس کے مواد کا ذمہ دار نہیں بیرونی لنکس کے بارے میں ہماری پالیسی' in text):
      copy_flag = False
    elif ('یہ بھی پڑھیے' in text):
      copy_flag = False
    elif ('اسی بارے میں' in text):
      copy_flag = False
    elif ('مزید پڑھیے' in text):
      copy_flag = False
    elif ('Twitter کا مواد دکھانے کی اجازت دی جائے' in text):
      copy_flag = False
    elif (link):
      copy_flag = False
    if (copy_flag):
      paras.append(text)
    #Saving complete article by first joining the paras of article
    summary['article'] = paras
  return summary

def update_articles(ArticleObj):
  name = 'Articles.jsonl'

  existing_articles = []
  if os.path.exists(drivePath+name):
    existing_articles = read_jsonl(drivePath+name)

  for obj in ArticleObj:
    existing_articles.append(obj)
  with open(drivePath+name, 'w', encoding='utf-8') as f:
    for a in existing_articles:
      json.dump(a, f, ensure_ascii=False)
      f.write("\n")
  print(name,' file appended..with ', len(ArticleObj), ' records!')

# Func for URL Const from url in Summaries
def make_URL(url):
  base_url = 'https://www.bbc.com'
  return base_url+url

In [ ]:
name = 'Summaries.jsonl'
if os.path.exists(drivePath+name):
  existing_summaries = read_jsonl(drivePath+name)
Articles = []
count = 0
for s in existing_summaries:
  tmp = extract_article(s)
  Articles.append(tmp)
  count += 1
  print('Article No ', count, ' Complete..')
  if count % 1000 == 0:
    time.sleep(random.randint(20, 30))

update_articles(Articles)

Retrieved url: https://www.bbc.com/urdu/articles/cv20nxzl544o
Article No  1  Complete..
Retrieved url: https://www.bbc.com/urdu/articles/c109pqg9v1vo
Article No  2  Complete..
Retrieved url: https://www.bbc.com/urdu/articles/cj78ev79mdmo
Article No  3  Complete..
Retrieved url: https://www.bbc.com/urdu/articles/c3gl4pp0gzgo
Article No  4  Complete..
Retrieved url: https://www.bbc.com/urdu/articles/c2q3k4nq39no
Article No  5  Complete..
Retrieved url: https://www.bbc.com/urdu/articles/ceqenw2e12lo
Article No  6  Complete..
Retrieved url: https://www.bbc.com/urdu/articles/c88e33q29d2o
Article No  7  Complete..
Retrieved url: https://www.bbc.com/urdu/articles/clm0x7pxg0do
Article No  8  Complete..
Retrieved url: https://www.bbc.com/urdu/articles/cd1kyp510xlo
Article No  9  Complete..
Retrieved url: https://www.bbc.com/urdu/articles/c807p1xd40wo
Article No  10  Complete..
Retrieved url: https://www.bbc.com/urdu/articles/cl7x2j58rvpo
Article No  11  Complete..
Retrieved url: https://www.bbc